# Le connecteur de Shaeffer

Marc Lorenzi

28 septembre 2022

## 1. Un peu de théorie

### 1.1 Ensembles complets de connecteurs

**Définition.** Un *ensemble complet* de connecteurs est un ensemble $\Gamma$ de connecteurs tel que toute formule de la logique des propositions soit équivalente à une formule ne faisant intervenir que des connecteurs de l'ensemble $\Gamma$.

**Proposition 1.** Soient $\Gamma$ un ensemble complet de connecteurs et $\Gamma'$ un ensemble de connecteurs. Alors $\Gamma'$ est un ensemble complet de connecteurs si et seulement si les connecteurs de $\Gamma$ peuvent être exprimés à l'aide de ceux de $\Gamma'$.

**Proposition.** $\Gamma_0=\{\lnot,\lor,\land\}$ est un ensemble complet de connecteurs.

**Démonstration.** Nous ne ferons pas la preuve ici. Par exemple, toute formule est équivalente à une formule sous *forme normale disjonctive*.

**Proposition.** $\{\lnot,\land\}$, $\{\lnot,\lor\}$ et $\{\lnot,\Rightarrow\}$ sont des ensembles complets de connecteurs.

**Démonstration.** Posons $\Gamma_1=\{\lnot,\land\}$. Soient $A$ et $B$ deux propositions. On a par l'une des lois de Morgan, $A\lor B\equiv \lnot(\lnot A\land\lnot B)$. Tous les connecteurs de $\Gamma_0$ peuvent s'exprimer à l'aide des connecteurs de $\Gamma_1$. Or, $\Gamma_0$ est un système complet de connecteurs, donc $\Gamma_1$ en est un aussi.

On conclut de même avec les ensembles $\{\lnot,\lor\}$ et $\{\lnot,\Rightarrow\}$ en remarquant que $A\land B\equiv \lnot(\lnot A\lor\lnot B)$ et $A\lor B\equiv \lnot A\Rightarrow B$.

**Proposition.** Les ensembles $\{\lnot\}$, $\{\land\}$, $\{\lor\}$ et $\{\Rightarrow\}$ ne sont **pas** des ensembles complets de connecteurs.

### 1.2 Le connecteur de Shaeffer

Le connecteur de Shaeffer, appelé aussi NAND, est défini, pour toutes propositions $A$ et $B$, par

$$A\uparrow B=\lnot(A\land B)$$

**Proposition.** $\{\uparrow\}$ est un ensemble complet de connecteurs.

**Démonstration.** Soient $A$ et $B$ deux propositions. On a 

$$\lnot A\equiv \lnot A\land \lnot A\equiv\lnot(A\land A)=A\uparrow A$$

On a également

$$A\lor B\equiv \lnot(\lnot A\land \lnot B)=\lnot A\uparrow\lnot B\equiv (A\uparrow A)\uparrow(B\uparrow B)$$

Comme $\{\lnot,\lor\}$ est un ensemble complet de connecteurs, $\{\uparrow\}$ en est aussi un.

## 2. Connecteurs binaires et connecteur de Shaeffer

### 2.1 Introduction

Soit $\varphi$ une formule logique n'utilisant que le connecteur $\uparrow$. Nous appellerons une telle formule une *formule de Shaeffer*. On a deux possibilités.

- Cas 1, $\varphi$ est une variable propositionnelle.
- Cas 2, $\varphi=\varphi'\uparrow\varphi''$, où $\varphi'$ et $\varphi''$ sont des formules de Shaeffer.

Dans le cas 1, nous représentons $\varphi$ en Python par le couple `('var', X)` où $X$ est un entier naturel. Dans le cas 2, si $f'$ et $f''$ sont les représentations en Python des formules $\varphi'$ et $\varphi''$, nous représentons $\varphi$ en Python par le couple $(f',f'')$.

Nous appellerons *complexité* de la formule $\varphi$ le nombre d'occurences du connecteur $\uparrow$ dans $\varphi$.

In [1]:
def est_atomique(f):
    return f[0] == 'var'

In [2]:
def complexite(f):
    if est_atomique(f): return 0
    else:
        c1 = complexite(f[0])
        c2 = complexite(f[1])
        return c1 + c2 + 1

Définissons aussi la *profondeur* d'une expression. C'est la hauteur de l'arbre qui représente cette expression.

In [3]:
def profondeur(f):
    if est_atomique(f):
        return 0
    else:
        return 1 + max(profondeur(f[0]), profondeur(f[1]))

La fonction `formules` prend en paramètres deux entier naturel $n$ et $p$. Elle énumère toutes les formules de Shaeffer de complexité $n$ à $p$ variables.

In [4]:
def formules(n, p):
    if n == 0:
        for k in range(p):
            yield ('var', k)
    else:
        for k in range(n):
            for g in formules(k, p):
                for h in formules(n - 1 - k, p):
                    yield (g, h)

Voici toutes les formules de Shaeffer de complexité 2.

In [5]:
for f in formules(2, 2):
    print(f)

(('var', 0), (('var', 0), ('var', 0)))
(('var', 0), (('var', 0), ('var', 1)))
(('var', 0), (('var', 1), ('var', 0)))
(('var', 0), (('var', 1), ('var', 1)))
(('var', 1), (('var', 0), ('var', 0)))
(('var', 1), (('var', 0), ('var', 1)))
(('var', 1), (('var', 1), ('var', 0)))
(('var', 1), (('var', 1), ('var', 1)))
((('var', 0), ('var', 0)), ('var', 0))
((('var', 0), ('var', 0)), ('var', 1))
((('var', 0), ('var', 1)), ('var', 0))
((('var', 0), ('var', 1)), ('var', 1))
((('var', 1), ('var', 0)), ('var', 0))
((('var', 1), ('var', 0)), ('var', 1))
((('var', 1), ('var', 1)), ('var', 0))
((('var', 1), ('var', 1)), ('var', 1))


Tout ceci est peu lisible. Écrivons donc une fonction transformant une formule de Shaeffer en une chaîne de caractères. Utilisons une barre verticale pour représenter le connecteur de Shaeffer.  On suppose que $p\le 26$ et que les variables sont $A$, $B$, etc.

In [6]:
def vers_chaine(f):
    if est_atomique(f):
        return chr(65 + f[1])
    else:
        s1 = vers_chaine(f[0])
        s2 = vers_chaine(f[1])
        if not est_atomique(f[0]):
            s1 = '(' + s1 + ')'
        if not est_atomique(f[1]):
            s2 = '(' + s2 + ')'
        return s1 + '|' + s2

Voici à nouveau les formules de Shaeffer de complexité 2 à 2 variables.

In [10]:
for f in formules(2, 2):
    print(vers_chaine(f))

A|(A|A)
A|(A|B)
A|(B|A)
A|(B|B)
B|(A|A)
B|(A|B)
B|(B|A)
B|(B|B)
(A|A)|A
(A|A)|B
(A|B)|A
(A|B)|B
(B|A)|A
(B|A)|B
(B|B)|A
(B|B)|B


C'est beaucoup mieux.

### 2.2 Le nombre de formules de Shaeffer

Une formule de Shaeffer de complexité $n$ à $p$ variables peut être représentée par un arbre binaire ayant $n$ noeuds internes. C'est d'ailleurs ce que nous avions plus ou moins dans notre représentation en Python. Il existe $C_n$ tels arbres binaires, où $C_n$ est le $n$ième *nombre de Catalan* :

$$C_n=\frac 1 {n+1}\binom {2n} n$$

Il faut ensuite étiqueter les feuilles de l'arbre, qui sont au nombre de $n+1$, par une variable. Cela donne donc $p^{n+1}$ étiquetages différents pour chaque arbre. Ainsi, le nombre de formules de Shaeffer de Complexité $n$ est

$$F_n=\binom {2n} n\frac {p^{n+1}} {n+1}$$

Remarquons que

$$\binom {2n}n\sim \frac {2^{2n}}{\sqrt{\pi n}}$$

On a donc

$$F_n\sim\frac {2^{2n}p^{n+1}}{n\sqrt{\pi n}}$$

Inutile, donc, d'espérer des miracles des fonctions que nous allons écrire. Le nombre de formules de Shaeffer de complexité $n$ croît exponentiellement avec $n$. Faisons un petit essai numérique.

In [11]:
def power_dn(n, k):
    p = 1
    for j in range(k):
        p *= n - j
    return p

In [12]:
def binom(n, k):
    return power_dn(n, k) // power_dn(k, k)

In [13]:
print([binom(6, k) for k in range(7)])

[1, 6, 15, 20, 15, 6, 1]


In [14]:
def nb_formules_shaeffer(n, p):
    return binom(2 * n, n) * p ** (n + 1) // (n + 1)

In [15]:
for n in range(10):
    print(n, nb_formules_shaeffer(n, 2))

0 2
1 4
2 16
3 80
4 448
5 2688
6 16896
7 109824
8 732160
9 4978688


Il y a presque 5 millions de formules de Shaeffer de complexité 9 à 2 variables.

### 2.3 Évaluer une formule de Shaeffer

Soient $x,y\in\{0,1\}$. La fonction `nand` renvoie 0 si $x=y=1$, et $1$ sinon.

In [16]:
def nand(x, y):
    return 1 - x * y

La fonction `eval_formule` prend en paramètre une formule $f$ et une liste `e` d'entiers valant 0 ou 1. Elle affecte à la variable $k$ la valeur de vérité `e[k]`, et renvoie la valeur de vérité de $f$.

In [17]:
def eval_formule(f, e):
    if est_atomique(f): return e[f[1]]
    else:
        u = eval_formule(f[0], e)
        v = eval_formule(f[1], e)
        return nand(u,v)

La fonction `environnements` prend un entier $p$ en paramètre. Elle énumère la liste des listes de $p$ éléments de $\{0,1\}$, dans l'ordre lexicographique.

In [18]:
def environnements(p):
    if p == 0:  yield []
    else:
        for e in environnements(p - 1):
            for x in [0, 1]:
                yield e + [x]

In [19]:
for e in environnements(3): print(e)

[0, 0, 0]
[0, 0, 1]
[0, 1, 0]
[0, 1, 1]
[1, 0, 0]
[1, 0, 1]
[1, 1, 0]
[1, 1, 1]


La fonction `table_formule` prend en paramètre une formule de Shaeffer $f$ à $p$ variables et l'entier $p$ et renvoie sa table sous la forme d'une liste de $2^p$ éléments. 

In [20]:
def table_formule(f, p):
    return [eval_formule(f, e) for e in environnements(p)]

In [21]:
for f in formules(2, 2):
    print(vers_chaine(f), table_formule(f, 2))

A|(A|A) [1, 1, 1, 1]
A|(A|B) [1, 1, 0, 1]
A|(B|A) [1, 1, 0, 1]
A|(B|B) [1, 1, 0, 1]
B|(A|A) [1, 0, 1, 1]
B|(A|B) [1, 0, 1, 1]
B|(B|A) [1, 0, 1, 1]
B|(B|B) [1, 1, 1, 1]
(A|A)|A [1, 1, 1, 1]
(A|A)|B [1, 0, 1, 1]
(A|B)|A [1, 1, 0, 1]
(A|B)|B [1, 0, 1, 1]
(B|A)|A [1, 1, 0, 1]
(B|A)|B [1, 0, 1, 1]
(B|B)|A [1, 1, 0, 1]
(B|B)|B [1, 1, 1, 1]


### 2.4 Trouver une formule de Shaeffer dont la table est connue

La fonction `trouver_formule` prend en paramètre une table de vérité `tbl` (i.e. une liste de 4 éléments valant 0 ou 1). Elle renvoie une formule de Shaeffer dont la table est `tbl`. La formule renvoyée est de complexité minimale.

In [22]:
def log2(n):
    p = 0
    m = 1
    while m != n:
        p = p + 1
        m = m * 2
    return p

In [23]:
def trouver_formule(tbl):
    p = log2(len(tbl))
    n = 0
    while True:
        for f in formules(n, p):
            if table_formule(f, p) == tbl: return f
        n += 1

Essayons avec la table du connecteur $\land$.

In [24]:
f = trouver_formule([0,0,0,1])
print(complexite(f), profondeur(f), vers_chaine(f))

3 2 (A|B)|(A|B)


Voici, pour toutes les tables possibles de connecteurs binaires, une formule ne faisant intervenir que le connecteur $\uparrow$.

In [25]:
cpt = 0
for e in environnements(4):
    print('%3d %s %s' % (cpt, e, vers_chaine(trouver_formule(e))))
    cpt += 1

  0 [0, 0, 0, 0] (A|(A|A))|(A|(A|A))
  1 [0, 0, 0, 1] (A|B)|(A|B)
  2 [0, 0, 1, 0] (A|(A|A))|(A|(A|B))
  3 [0, 0, 1, 1] A
  4 [0, 1, 0, 0] (A|(A|A))|(B|(A|A))
  5 [0, 1, 0, 1] B
  6 [0, 1, 1, 0] (A|(A|B))|(B|(A|A))
  7 [0, 1, 1, 1] (A|A)|(B|B)
  8 [1, 0, 0, 0] (A|(A|A))|((A|A)|(B|B))
  9 [1, 0, 0, 1] (A|B)|((A|A)|(B|B))
 10 [1, 0, 1, 0] B|B
 11 [1, 0, 1, 1] B|(A|A)
 12 [1, 1, 0, 0] A|A
 13 [1, 1, 0, 1] A|(A|B)
 14 [1, 1, 1, 0] A|B
 15 [1, 1, 1, 1] A|(A|A)


### 2.5 Toutes les solutions

La formule renvoyée par `trouver_formule` est loin d'être unique. La fonction `toutes_formules` prend en paramètres une table `tbl` et un entier $n$. Elle énumère toutes les formules de Shaeffer de complexité $n$ dont la table est `tbl`.

In [26]:
def toutes_formules(tbl, n, p):
    for f in formules(n, p):
        if table_formule(f, p) == tbl: yield f

Voici par exemple toutes les formules de Shaeffer de complexité 2 équivalentes à $A\Rightarrow B$. Il y en a 6.

In [27]:
for f in toutes_formules([1, 1, 0, 1], 2, 2):
    print(vers_chaine(f))

A|(A|B)
A|(B|A)
A|(B|B)
(A|B)|A
(B|A)|A
(B|B)|A


Autre exemple, $A\Leftrightarrow B$.

In [28]:
vers_chaine(trouver_formule([1, 0, 0, 1]))

'(A|B)|((A|A)|(B|B))'

In [29]:
cpt = 1
for f in toutes_formules([1, 0, 0, 1], 5, 2):
    print(cpt, vers_chaine(f))
    cpt += 1

1 (A|B)|((A|A)|(B|B))
2 (A|B)|((B|B)|(A|A))
3 (B|A)|((A|A)|(B|B))
4 (B|A)|((B|B)|(A|A))
5 ((A|A)|(B|B))|(A|B)
6 ((A|A)|(B|B))|(B|A)
7 ((B|B)|(A|A))|(A|B)
8 ((B|B)|(A|A))|(B|A)


Enfin, $A\downarrow B=\lnot(A\lor B)$.

In [30]:
f = trouver_formule([1, 0, 0, 0])
print(complexite(f), profondeur(f), vers_chaine(f))

6 3 (A|(A|A))|((A|A)|(B|B))


In [31]:
cpt = 1
for f in toutes_formules([1, 0, 0, 0], 6, 2):
    print(cpt, vers_chaine(f))
    cpt += 1

1 (A|(A|A))|((A|A)|(B|B))
2 (A|(A|A))|((B|B)|(A|A))
3 (B|(B|B))|((A|A)|(B|B))
4 (B|(B|B))|((B|B)|(A|A))
5 ((A|A)|A)|((A|A)|(B|B))
6 ((A|A)|A)|((B|B)|(A|A))
7 ((B|B)|B)|((A|A)|(B|B))
8 ((B|B)|B)|((B|B)|(A|A))
9 ((A|A)|(B|B))|(A|(A|A))
10 ((A|A)|(B|B))|(B|(B|B))
11 ((A|A)|(B|B))|((A|A)|A)
12 ((A|A)|(B|B))|((B|B)|B)
13 ((B|B)|(A|A))|(A|(A|A))
14 ((B|B)|(A|A))|(B|(B|B))
15 ((B|B)|(A|A))|((A|A)|A)
16 ((B|B)|(A|A))|((B|B)|B)
